# Farmers optimization example

### *Author: Tim Diller*



## 0) Introduction

This is a simple introduction how to formulate and solve linear and mixed integer problems (LPs and MIPs respectively) in python using PuLP.



## Problem statement


There is a farmer who has 100 hectares, and is wondering what to plant

- he can plant apples and wine

- apples yield 300 eur per hectare
- wine yields 400 eur per hectare

- both need to be harvested in October

- there are 9 * 31 work hours in October (farmers don't know what a weekend is)
- the farmer has 1 helper

- apples need 3 hours/hectare to harvest
- wine needs 7 hours/hectare to harvest

- he cannot work overtime

Tractor constraint:

- in July, the wine needs to be protected from fungi, so a fungicide needs to be sprayed on the wine (not on the apples). This takes 5 hours/hectare, and the tractor is available for a total of 190 hours in July.




## 1) Explanation first coding steps (Import and variable definition)

We want to formulate this problem as a linear problem (LP) in python using PuLP.

First we import the libraries.

In [ ]:
import plotly.graph_objects as go
import numpy as np

# pulp is not a colab default package, so it has to be installed first via the python package manager pip.
# lines starting with a ! are shell commands, not python code, however, this ONLY works in Colab, not in normal python
!pip install pulp

import pulp as pl

Next we need to define all variables that we need for the constraints.

In [ ]:
area_field = 100  # [ha]
yield_apple = 300  # [$/ha/year]
yield_wine = 400  # [$/ha/year]
hours_per_hectare_apple = 3  # [hour/ha]
hours_per_hectare_wine = 7  # [hour/ha]
hours_per_day = 8  # [hour/day]
days_per_month = 31  # [day/month]
amount_workers = 2  # [-]
max_hours = days_per_month * hours_per_day * amount_workers  # [hour/month]

tractor_hours = 270  # [hour]
hours_per_hectare_fungicide = 5  # [hour/ha]

# lastly, we define how detailed we want the plot
amount_points_plotting = 300  # [-]

then we define a function that is calculating the profit that we get as a function of the amount of apples and wine we plant.

In [ ]:

def calculate_profit(area_apple, area_wine):
    return area_apple * yield_apple + area_wine * yield_wine

## 2) Plot the problem

To illustrate the problem, we make a few plots.

### 2.1) Goal function

we define x as the amount of apple hectares, and y as the amount of wine hectares, and colour code the profit as a function of the amount of apples and wine that are planted.

In [ ]:
# Create the meshgrid
x = np.linspace(0, 100, amount_points_plotting)
y = np.linspace(0, 100, amount_points_plotting)
X, Y = np.meshgrid(x, y)

# Calculate the profit for each point in the meshgrid
Z = calculate_profit(X, Y)

# Create the 2D plot
heatmap_trace = go.Heatmap(x=x, y=y, z=Z, colorscale='Rainbow')
fig = go.Figure(data=[heatmap_trace])  # Using Heatmap for color representation
fig.show()


### 2.2) Area limit
So far so easy. The more I plant, the more I earn. But a LOT of the solutions probably violate at least one constraint. So we can also plot the relevant constraints. The first constraint is that there are only 100 hectares to be planted, so the sum of x and y cannot exceed hour hectare limit. We can visualize the limit on the plot.

In [ ]:
area_limit_trace = go.Scatter(x=[0, area_field], y=[area_field, 0], line=dict(color='orange', width=3), name='area limit')
fig = go.Figure(data=[heatmap_trace, area_limit_trace])
fig.update_layout(title='Profit vs. Area of Apples and Wine',
                  width=1000,  # Set the width
                  height=1000, # Set the height
                  xaxis_title='Area of Apples [ha]',
                  yaxis_title='Area of Wine [ha]',
                  legend=dict(x=1, y=1, xanchor='right', yanchor='top'))


fig.show()

### 2.3) Time limit
but there is also the second limitation: he can only harvest so much, before the fruits degrade:

the constraint is = area_apple * hours_per_hectare_apple + area_wine * hours_per_hectare_wine <= max_hours

in order to plot the constraint, we need to bring it into a f(x) = y constraint

(we will only plot the line where it is binding)



In [ ]:
# we can define how much wine is allowed as a function of the amount of apples planted
def max_allowed_wine(area_apples):
    return (max_hours - area_apples * hours_per_hectare_apple) / hours_per_hectare_wine

Now we can use the function to generate a line.

In [ ]:
apple_list = [x for x in range(102)]
wine_list = [max_allowed_wine(x) for x in apple_list]
work_limit_trace = go.Scatter(x=apple_list, y=wine_list, line=dict(color='red', width=3), name='work limit')
fig = go.Figure(data=[heatmap_trace, area_limit_trace, work_limit_trace])
fig.update_layout(title='Profit vs. Area of Apples and Wine',
                  width=1000,  # Set the width
                  height=1000, # Set the height
                  xaxis_title='Area of Apples [ha]',
                  yaxis_title='Area of Wine [ha]',
                  legend=dict(x=1, y=1, xanchor='right', yanchor='top'))
fig.show()


### 2.4 Tractor limit
Lastly, we visualize the tractor restriction. This in effect limits the amount of wine we can plant

In [ ]:
max_wine = tractor_hours / hours_per_hectare_fungicide

wine_limit_trace = go.Scatter(x=[0, area_field], y=[max_wine, max_wine], line=dict(color='purple', width=3), name='tractor limit')
fig = go.Figure(data=[heatmap_trace, area_limit_trace, work_limit_trace, wine_limit_trace, ])
fig.update_layout(title='Profit vs. Area of Apples and Wine',
                  xaxis_title='Area of Apples [ha]',
                  yaxis_title='Area of Wine [ha]',
                  width=1000,  # Set the width
                  height=1000,
                  legend=dict(x=1, y=1, xanchor='right', yanchor='top'))
fig.show()

to make the visualization prettier, we can also update the result function to only return values if all conditions are met, and return None afterwards.


In [ ]:
def calculate_profit_with_limits(area_apple, area_wine):
    if area_apple + area_wine > area_field:
        return None

    if area_apple * hours_per_hectare_apple + area_wine * hours_per_hectare_wine > max_hours:
        return None

    if area_wine > max_wine:
        return None

    return area_apple * yield_apple + area_wine * yield_wine

### 2.5) Plotting the cutoff heatmap

And now we can recalculate the Z value, and replot our heatmap


In [ ]:
Z_complete = np.zeros((amount_points_plotting, amount_points_plotting))

for apple_index, area_apple in enumerate(x):
    for wine_index, area_wine in enumerate(y):
        Z_complete[wine_index, apple_index] = calculate_profit_with_limits(area_apple, area_wine)
heatmap_trace_cut = go.Heatmap(x=x, y=y, z=Z_complete, colorscale='Rainbow')
fig = go.Figure(data=[heatmap_trace_cut, area_limit_trace, work_limit_trace, wine_limit_trace])
fig.update_layout(title='Profit vs. Area of Apples and Wine',
                  xaxis_title='Area of Apples [ha]',
                  yaxis_title='Area of Wine [ha]',
                  width=1000,  # Set the width
                  height=1000, # Set the height
                  legend=dict(x=1, y=1, xanchor='right', yanchor='top'))
fig.show()

Based on this, we can now answer questions like:

- can the farmer help his profit by hiring someone else to help him with the harvest?
- how about renting another tractor?
- if a neighbouring farmer offers to rent him his 30 hectares for a price of 15k Eur/year, should he take the deal?

## 3 solving this using PuLP

we can now formulate and solve this optimization problem using PuLP, with CBC as a solver

In [ ]:
# Create the problem
prob = pl.LpProblem("Farmers_Optimization", pl.LpMaximize)

# Define the decision variables
area_apple = pl.LpVariable("Area_Apple", 0, None, pl.LpInteger)
area_wine = pl.LpVariable("Area_Wine", 0, None, pl.LpInteger)

# Define the objective function (profit)
prob += area_apple * yield_apple + area_wine * yield_wine, "Total_Profit"

# Define the constraints
prob += area_apple + area_wine <= area_field, "Area_Constraint"
prob += area_apple * hours_per_hectare_apple + area_wine * hours_per_hectare_wine <= max_hours, "Work_Constraint"
prob += area_wine <= max_wine, "Tractor_Constraint"

# Solve the problem
prob.solve()

# Print the results
print("Status:", pl.LpStatus[prob.status])
print("Optimal Area for Apples:", pl.value(area_apple), "hectares")
print("Optimal Area for Wine:", pl.value(area_wine), "hectares")
print("Maximum Profit:", pl.value(prob.objective), "EUR")

Status: Optimal
Optimal Area for Apples: 51.0 hectares
Optimal Area for Wine: 49.0 hectares
Maximum Profit: 34900.0 EUR


## 3.2 Plot the optimal solution

And now we can replot the optimization problem, with all restrictions, and add the optimal point as a scatter on the plot.


In [ ]:
# prompt: replot the optimization problem from above with all the constraints, and add the optimal point found by pulp as a scatter point.

# Add the optimal point as a scatter plot
optimal_apple = pl.value(area_apple)
optimal_wine = pl.value(area_wine)

optimal_point_trace = go.Scatter(x=[optimal_apple], y=[optimal_wine], mode='markers', marker=dict(size=10, color='black'), name='Optimal Point')

fig = go.Figure(data=[heatmap_trace_cut, area_limit_trace, work_limit_trace, wine_limit_trace, optimal_point_trace])
fig.update_layout(title='Profit vs. Area of Apples and Wine',
                  xaxis_title='Area of Apples [ha]',
                  yaxis_title='Area of Wine [ha]',
                  width=1000,  # Set the width
                  height=1000, # Set the height
                  legend=dict(x=1, y=1, xanchor='right', yanchor='top'))
fig.show()

# 4 Conclusion
The plot visually demonstrates that the optimal solution to the farmer's problem lies at the intersection of two constraints: the area limit (orange line) and the tractor limit (purple line). This is a characteristic feature of Linear Programming (LP) problems. The feasible region, represented by the area where all constraints are satisfied, forms a polygon. The optimal solution always resides at one of the vertices (corners) of this polygon, which are formed by the intersection of constraints.

The simplex algorithm leverages this property to efficiently find the optimal solution. It starts at an initial feasible vertex and iteratively moves to adjacent vertices with better objective function values. By systematically exploring these vertices, the algorithm guarantees convergence to the optimal solution, which is always located at a vertex where two or more constraints intersect.

In this specific case, the intersection of the area limit and the tractor limit represents the point where the farmer maximizes profit while adhering to all constraints. This highlights the importance of understanding the interplay between constraints and the objective function in LP problems. By carefully analyzing these interactions, we can identify the optimal allocation of resources and achieve the desired outcome.

# 5 Addon: Turning it into a Mixed Integer Problem (MIP) and solving it

Here you can see my conversation with Gemini, who tries to generate the MIP and fails, as he does not recognize that pulp lingo is different from general algebra in what you can do.

In [ ]:
# prompt: please reformulate the optimization problem as a MILP, where the area in hectares for both apples and oranges has to be a multiple of 5 hectares (so an integer that is divisible by 5 rather than a float)

import plotly.graph_objects as go
import numpy as np
import pulp as pl

# ... (rest of the code remains the same)

# ## 3) solving this using PuLP (Modified for MILP)

# Create the problem
prob = pl.LpProblem("Farmers_Optimization_MILP", pl.LpMaximize)

# Define the decision variables as integer multiples of 5
area_apple = pl.LpVariable("Area_Apple", 0, None, pl.LpInteger)
area_wine = pl.LpVariable("Area_Wine", 0, None, pl.LpInteger)

# Add constraints to ensure divisibility by 5
prob += area_apple % 5 == 0, "Apple_Divisibility"
prob += area_wine % 5 == 0, "Wine_Divisibility"


# Define the objective function (profit)
prob += area_apple * yield_apple + area_wine * yield_wine, "Total_Profit"

# Define the constraints
prob += area_apple + area_wine <= area_field, "Area_Constraint"
prob += area_apple * hours_per_hectare_apple + area_wine * hours_per_hectare_wine <= max_hours, "Work_Constraint"
prob += area_wine <= max_wine, "Tractor_Constraint"

# Solve the problem
prob.solve()

# Print the results
print("Status:", pl.LpStatus[prob.status])
print("Optimal Area for Apples:", pl.value(area_apple), "hectares")
print("Optimal Area for Wine:", pl.value(area_wine), "hectares")
print("Maximum Profit:", pl.value(prob.objective), "EUR")

# ... (rest of the plotting code remains the same)

TypeError: unsupported operand type(s) for %: 'LpVariable' and 'int'

Here is the updated query, where I explain in more detail what I want him to do and how he needs to resolve the problem.

In [ ]:
# prompt: your code does not work, as the % operator cannot be used in pulp. You will need to add a helper_apple and helper_wine variable that are integers between 0 and 20, and mandate that area_apple * 5 == helper_apple, and area_wine * 5 == helper_wine

# ... (rest of the code remains the same)

# ## 3) solving this using PuLP (Modified for MILP)

# Create the problem
prob = pl.LpProblem("Farmers_Optimization_MILP", pl.LpMaximize)

# Define the decision variables as integers
area_apple = pl.LpVariable("Area_Apple", 0, None, pl.LpInteger)
area_wine = pl.LpVariable("Area_Wine", 0, None, pl.LpInteger)

# Define helper variables
helper_apple = pl.LpVariable("Helper_Apple", 0, 20, pl.LpInteger)
helper_wine = pl.LpVariable("Helper_Wine", 0, 20, pl.LpInteger)


# Define the objective function (profit)
prob += area_apple * yield_apple + area_wine * yield_wine, "Total_Profit"

# Define the constraints
prob += area_apple + area_wine <= area_field, "Area_Constraint"
prob += area_apple * hours_per_hectare_apple + area_wine * hours_per_hectare_wine <= max_hours, "Work_Constraint"
prob += area_wine <= max_wine, "Tractor_Constraint"

# Add constraints for divisibility by 5 using helper variables
prob += helper_apple * 5 == area_apple
prob += helper_wine * 5 == area_wine

# Solve the problem
prob.solve()

# Print the results
print("Status:", pl.LpStatus[prob.status])
print("Optimal Area for Apples:", pl.value(area_apple), "hectares")
print("Optimal Area for Wine:", pl.value(area_wine), "hectares")
print("Maximum Profit:", pl.value(prob.objective), "EUR")

# ... (rest of the plotting code remains the same)

Status: Optimal
Optimal Area for Apples: 55.0 hectares
Optimal Area for Wine: 45.0 hectares
Maximum Profit: 34500.0 EUR


Now we can replot the problem with the optimal point again put in as a scatter.

In [ ]:
# prompt: and now replot the problem with the new optimal point.

# Add the optimal point as a scatter plot
optimal_apple = pl.value(area_apple)
optimal_wine = pl.value(area_wine)

optimal_point_trace = go.Scatter(x=[optimal_apple], y=[optimal_wine], mode='markers', marker=dict(size=10, color='black'), name='Optimal Point')

fig = go.Figure(data=[heatmap_trace_cut, area_limit_trace, work_limit_trace, wine_limit_trace, optimal_point_trace])
fig.update_layout(title='Profit vs. Area of Apples and Wine',
                  xaxis_title='Area of Apples [ha]',
                  yaxis_title='Area of Wine [ha]',
                  width=1000,  # Set the width
                  height=1000, # Set the height
                  legend=dict(x=1, y=1, xanchor='right', yanchor='top'))
fig.show()

### Conclusion

While Linear Programming (LP) problems can be efficiently solved using the simplex algorithm, Mixed-Integer Programming (MIP) problems introduce additional complexity due to the requirement of integer solutions. This restriction prevents the direct application of the simplex algorithm, making MIPs generally harder to solve.

In certain cases, the optimal integer solution can differ significantly from the linear solution obtained by relaxing the integer constraints. This discrepancy arises because the integer solution space is a subset of the continuous solution space, and the optimal solution may not lie on the boundary of the feasible region.

Despite the computational challenges, MIPs are crucial for modeling real-world problems where discrete decisions are involved. For instance, in agriculture, farmers often deal with a finite number of fields and must choose one crop per field. In manufacturing, it's impossible to produce half a bike or fill half a work shift. These scenarios necessitate integer solutions, making MIPs a powerful tool for optimization in various domains.

Although MIPs are generally harder to solve, advancements in algorithms and computational power have made it possible to tackle increasingly complex problems. By incorporating integer constraints, MIPs provide a more realistic and accurate representation of real-world scenarios, enabling better decision-making and resource allocation.

In conclusion, while MIPs pose computational challenges due to the integer requirements, they are essential for modeling and solving real-world problems where discrete decisions are involved. By accurately representing these constraints, MIPs enable more effective optimization and lead to better outcomes in various domains.

## 6 Notes on Gemini

Gemini significantly reduced the time it took me to create this workbook. However, it also had limitations. It wasnt able to make the constraint an integer constraint without me telling him HOW to do it. It also failed to recognize WHICH of the restrictions were binding. (when I asked it, it gave me the wrong result).

In conclusion: Its a great help, but it doesnt get you out of learning how to read and write code (and more crucially, understand the logic) yourself.